---

# S06E00 : Concurrency - Introduction to concurrency with Python

Cyril Desjouy

--- 

## 1. Introduction


From [wikipedia](https://en.wikipedia.org/wiki/Concurrency_(computer_science)):

>*In computer science, **concurrency** is the ability of different parts or units of a program, algorithm, or problem to be executed out-of-order or in partial order, without affecting the final outcome. This allows for parallel execution of the concurrent units, which can significantly improve overall speed of the execution in multi-processor and multi-core systems.*

In *synchronous* operations, the different parts of a program are executed one after the other. A task, once scheduled, must be completed before we can proceed to the next task. The operations are called *blocking* and must therefore follow one another. In the context of *asynchronous* operations, the different parts of a program can be executed concurrently. The operations are then *non-blocking*. A *task* can indeed start its execution while another has not yet completed its own. It is this principle that is referred to as *concurrency* in computer science.

In other words, *concurrency* implies that several *tasks* progress together. Python supports two forms of *concurrency* illustrated in Figure 1 and detailed below.

* Several *tasks* are executed in **parallel**, at the same time: we talk about **process** and ***multiprocessing***.
* Several *tasks* are executed **alternately**: we then speak of **thread** and ***threading***.


```
                     ┌─────────────────────────────────────────────────────────┐
                     │        ┌──────────┐┌──────────┐┌────────┐┌─────────────┐│
       Threads:      ╞<Core 1>╡ Thread 1 ╞╡ Thread 2 ╞╡Thread 1╞╡  Thread 3   ╞╡
                     │        └──────────┘└──────────┘└────────┘└─────────────┘│
                     └─────────────────────────────────────────────────────────┘

                     ┌─────────────────────────────────────────────────────────┐
                     │        ┌─────────────┐┌─────────────┐┌────────────┐     │
                     ╞<Core 1>╡  Process 1  ╞╡  Process 3  ╞╡  Process 5 ╞══>══╡
       Processes:    │        └─────────────┘└─────────────┘└────────────┘     │
                     │        ┌───────────────┐┌─────────────────────────────--│
                     ╞<Core 2>╡   Process 2   ╞╡        Process 4              │
                     │        └───────────────┘└─────────────────────────────--│
                     └─────────────────────────────────────────────────────────┘
                                   Fig. 1: Threads vs. processes
```

## 2. `threading` and `asyncio`

### 2.1. Note on ***GIL***

Python has supported the use of *threads* since its inception with the `threading` module provided in the standard library. *Threads* allow tasks to be performed concurrently, but **not in parallel**. This limitation comes from the implementation of CPython itself and a mechanism called ***GIL*** (Global Interpreter Lock) which is a lock preventing the simultaneous execution of ***threads***. In other words, the ***GIL*** ensures that only one ***thread*** is active at any given time. However, the Python interpreter can switch from one ***thread*** to another to allow them to run concurrently.

To learn more about the *why* and *how* of ***GIL***, a very well written article is available on [realpython.org](https://realpython.com/python-gil/).

### 2.2. The threads

In Python, the management of *threads* is therefore provided by the `threading` module. The advantage of *threads* is that they are relatively easy to set up and share the same memory space. All *threads* from the same *processsus* can therefore read and write the same data efficiently. Knowing this, it is of course important to be vigilant about data access when manipulating several *threads*.


### 2.2. Coroutines

As we have seen, it is possible to implement non-blocking tasks using *threads*. Another idea is to use the principle of generators that use the keyword `yield` to suspend in a non-blocking way the execution of a generator function. It is from this mechanism that the coroutines and the module `asyncio` were born. The basic principle of `asyncio` is to use an event loop with a queue from which the loop pulls tasks and executes them.

It is ultimately the way in which the *threads* (or tasks in the case of `asyncio`) succeed each other that makes the real difference between `threading` and `asyncio`. When using `threading`, it is the operating system that manages the planning of *threads* and can interrupt them at any time to launch different ones. This is called the *preventive multi-tasking*. When using `asyncio`, tasks must cooperate by announcing when they are ready to be replaced. This is called the *cooperative multi-tasking*.

## 3. How to bypass the ***GIL***?

#### 3.1. `Multiprocessing`

As we have seen previously, Python cannot run *threads* in parallel. 
The most direct approach to parallel computing in Python is to use *processes*. A *process* can be seen as an *independent* program running in its own Python interpreter. Each process has its own resources (CPU, memory) and can of course have several threads.
Different processes can run simultaneously in different interpreters without interfering since they use isolated resources. This is called ***multiprocessing***. In Python, to use *processes* we use the eponymous module `multiprocessing`. 

It is important to note that there are some disadvantages to using *processes*:

* Data sharing between *processes* is slower and more complex than between *threads* since *processes* do not share memory space (so it takes I/O time to pass information between *processes*).
* The opening and closing of *processes* takes longer than those of *threads* since it is a matter of *"relaunching an interpreter "* for each *process*.

### 3.2. Other possibilities

Some languages do not have the limitation imposed by the ***GIL*** on the simultaneous execution of *threads*. This is the case, for example, of <i>C</i>, <i>C+++</i> or *Fortran* which can easily be interfaced with Python (see C API python, f2py module, etc.). The most generally adopted solution is however the use of the `cython` module which provides tools to locally bypass the ***GIL*** and therefore to propose <i><b>multi</b>-threading</i> directly in Python (via *openMP*).

## 4. Conclusion

### 4.1. CPU bound vs. I/O bound

All types of concurrent programming offered by Python are useful. But you still need to know which type to use for which task. In computer science, two types of tasks can be distinguished:

* **I/O-bound tasks** such as *communication with a slow device* (network connection, storage device,...)<br>
    => Acceleration possible by overlaying device waiting times.

* **CPU-bound tasks** such as *mathematical operations*:<br>
    => Acceleration possible by multiplying the calculation units (processors).

As a result, we will tend to use ***processes*** for applications related to ***CPU*** and ***threads*** for applications related to ***I/O***. The following rule is generally relevant:

* CPU-bound tasks: `multiprocessing`, `cython` (and `mpi4py` for computing clusters)
* Tasks related to fast I/O with few connections: `threading`
* tasks related to slow I/Os with many connections: `asyncio`

Regardless of the type of *concurrency* used, it is important to keep in mind that concurrent programming creates an additional layer of complexity. It is therefore essential to assess whether the potential acceleration is worth the extra effort. 

### 4.2. On the menu

The purpose of this series of notebooks is not to cover all the possibilities offered by Python in terms of concurrent programming. Many modules developed by the community are indeed dedicated to concurrent programming as specified on the page [competition of the official python wiki](https://wiki.python.org/moin/Concurrency/). The objective here is more to provide some keys concerning the modules classically used in concurrent programming in Python. The different concepts discussed are therefore:

* The `multiprocessing` module or how to use the *processes*?
* The `threading` module or how to use the *threads*?
* Synchronization primitives or how to synchronize *threads* and *processes*?
* The module `concurrent.futures` or how to simplify the management of *threads* and *processes* for simple applications?
* The module `asyncio` or how to use the *coroutines*?
* The `cython` module or how to optimize scientific codes and use *cython* to bypass the ***GIL***?
* The `mpi4py` module or how to run *processes* on several machines each having several processors?

## References

* [Realpython.org - Concurrency](https://realpython.com/python-concurrency/)
* [Masnun - Forms of concurrency](http://masnun.rocks/2016/10/06/async-python-the-different-forms-of-concurrency/)